# Работа со строковыми значениями

__Автор задач: Блохин Н.В. (NVBlokhin@fa.ru)__

Материалы:
* Макрушин С.В. Лекция "Работа со строковыми значениям"
* https://pyformat.info/
* https://docs.python.org/3/library/re.html
    * https://docs.python.org/3/library/re.html#flags
    * https://docs.python.org/3/library/re.html#functions
* https://pythonru.com/primery/primery-primeneniya-regulyarnyh-vyrazheniy-v-python
* https://kanoki.org/2019/11/12/how-to-use-regex-in-pandas/
* https://realpython.com/nltk-nlp-python/

## Лабораторная работа 6

### Форматирование строк

In [7]:
import numpy as np
import pandas as pd

1\. Загрузите данные из файла `recipes_sample.csv` (__ЛР2__) в виде `pd.DataFrame` `recipes` При помощи форматирования строк выведите информацию об id рецепта и времени выполнения 5 случайных рецептов в виде таблицы следующего вида:

    
    |      id      |  minutes  |
    |--------------------------|
    |    61178     |    65     |
    |    202352    |    80     |
    |    364322    |    150    |
    |    26177     |    20     |
    |    224785    |    35     |
    
Обратите внимание, что ширина столбцов заранее неизвестна и должна рассчитываться динамически, в зависимости от тех данных, которые были выбраны. 

In [47]:
recipes

name      id  minutes  \
0             george s at the cove  black bean soup   44123       90   
1                healthy for them  yogurt popsicles   67664       10   
2                      i can t believe it s spinach   38798       30   
3                              italian  gut busters   35173       45   
4          love is in the air  beef fondue   sauces   84797       25   
...                                             ...     ...      ...   
29995  zurie s holey rustic olive and cheddar bread  267661       80   
29996          zwetschgenkuchen  bavarian plum cake  386977      240   
29997   zwiebelkuchen   southwest german onion cake  103312       75   
29998                                   zydeco soup  486161       60   
29999        cookies by design   cookies on a stick  298512       29   

       contributor_id   submitted  n_steps  \
0               35193  2002-10-25      NaN   
1               91970  2003-07-26      NaN   
2                1533  2002-08-29      NaN   
3               22724  2002-07-27      NaN   
4                4470  2004-02-23      4.0   
...               ...         ...      ...   
29995          200862  2007-11-25     16.0   
29996          177443  2009-08-24      NaN   
29997          161745  2004-11-03      NaN   
29998          227978  2012-08-29      NaN   
29999          506822  2008-04-15      9.0   

                                             description  n_ingredients  
0      an original recipe created by chef scott meska...           18.0  
1      my children and their friends ask for my homem...            NaN  
2                these were so go, it surprised even me.            8.0  
3      my sister-in-law made these for us at a family...            NaN  
4      i think a fondue is a very romantic casual din...            NaN  
...                                                  ...            ...  
29995  this is based on a french recipe but i changed...           10.0  
29996  this is a traditional fresh plum cake, thought...           11.0  
29997  this is a traditional late summer early fall s...            NaN  
29998  this is a delicious soup that i originally fou...            NaN  
29999  i've heard of the 'cookies by design' company,...           10.0  

[30000 rows x 8 columns]

In [31]:
recipes = pd.read_csv("data/recipes_sample.csv", sep=',')
sample = recipes.sample(n=5)

max_id_width = max(len(str(x)) for x in sample["id"]) + 1
max_minutes_width = max(len(str(x)) for x in sample["minutes"]) + 1

header_template = "| {:^{}} | {:^{}} |".format("id", max_id_width, "minutes", max_minutes_width)
row_template = "| {:>{}} | {:>{}} |".format("{:" + str(max_id_width) + "}", max_id_width, "{:" + str(max_minutes_width) + "}", max_minutes_width)

print(header_template)
print("-" * (max_id_width + max_minutes_width + 7))
for _, row in sample.iterrows():
    print(row_template.format(row["id"], row["minutes"]))

|   id    | minutes |
-----------------
|      54800 |  65 |
|     215729 |  28 |
|      27381 |  10 |
|     256588 |  30 |
|     113176 |  25 |


2\. Напишите функцию `show_info`, которая по данным о рецепте создает строку (в смысле объекта python) с описанием следующего вида:

```
"Название Из Нескольких Слов"

1. Шаг 1
2. Шаг 2
----------
Автор: contributor_id
Среднее время приготовления: minutes минут
```

    
Данные для создания строки получите из файлов `recipes_sample.csv` (__ЛР2__) и `steps_sample.xml` (__ЛР3__). 
Вызовите данную функцию для рецепта с id `170895` и выведите (через `print`) полученную строку на экран.

In [78]:
import xml.etree.ElementTree as ET

tree = ET.parse("data/steps_sample.xml")
root = tree.getroot()
steps_data = []
for recipe in root.findall("recipe"):
    recipe_id = int(recipe.find("id").text)
    steps = [step.text for step in recipe.findall("step")]
    steps_data.append({"id": recipe_id, "steps": steps})

steps_df = pd.DataFrame(steps_data)

def show_info(recipe_id, recipes, steps_df):
    recipe = recipes.loc[recipes["id"]==recipe_id].iloc[0]
    steps = steps_df.loc[steps_df["id"]==recipe_id].iloc[0]["steps"]
    
    title = recipe["name"].title()
    steps_text = "\n".join(f"{i+1}. {step}" for i, step in enumerate(steps))
    author = recipe["contributor_id"]
    minutes = recipe["minutes"]
    
    result = (
        f"{title}\n\n"
        f"{steps_text}\n"
        f"{'-'*10}\n"
        f"Автор: {author}\n"
        f"Среднее время приготовления: {minutes} минут"
    )
    return result

recipe_id = 170895
info = show_info(recipe_id, recipes, steps_df)
print(info)

Leeks And Parsnips  Sauteed Or Creamed


----------
Автор: 8377
Среднее время приготовления: 27 минут


## Работа с регулярными выражениями

3\. Напишите регулярное выражение, которое ищет следующий паттерн в строке: число (1 цифра или более), затем пробел, затем слова: hour или hours или minute или minutes. Произведите поиск по данному регулярному выражению в каждом шаге рецепта с id 25082. Выведите на экран все непустые результаты, найденные по данному шаблону.

In [77]:
from bs4 import BeautifulSoup
import re

with open("data/steps_sample.xml", "r") as file:
    content = file.read()
    soup = BeautifulSoup(content, "xml")

recipe_id = "25082"
recipe = soup.find(lambda tag: tag.name == "recipe" and tag.find("id") and tag.find("id").text == recipe_id)
steps = [step.get_text() for step in recipe.find_all("step")]

pattern = r"(?i)\b\d+\s(?:hours?|minutes?)\b"

recipe_info = recipes.loc[recipes["id"] == int(recipe_id)].iloc[0]
print(f"Name: {recipe_info['name']}")
print(f"ID: {recipe_info['id']}")

print("Results:")
for i, step in enumerate(steps):
    result = re.findall(pattern, step)
    if result:
        print(f"Step {i + 1}: {result}")

Name: basic whole wheat bread
ID: 25082
Results:
Step 6: ['20 minutes']
Step 8: ['10 minutes']
Step 10: ['2 hours']
Step 14: ['10 minutes']
Step 17: ['20 minutes', '30 minutes']


4\. Напишите регулярное выражение, которое ищет шаблон вида "this..., but" _в начале строки_ . Между словом "this" и частью ", but" может находиться произвольное число букв, цифр, знаков подчеркивания и пробелов. Никаких других символов вместо многоточия быть не может. Пробел между запятой и словом "but" может присутствовать или отсутствовать.

Используя строковые методы `pd.Series`, выясните, для каких рецептов данный шаблон содержится в тексте описания. Выведите на экран количество таких рецептов и 3 примера подходящих описаний (текст описания должен быть виден на экране полностью).

In [79]:
pattern = r"^this[^A-Za-z0-9_]*\.{3}, ?but"

all_recipes = soup.find_all("recipe")

for recipe_soup in all_recipes:
    recipe_id = int(recipe_soup.find("id").text)
    steps = [step.get_text() for step in recipe_soup.find_all("step")]

    print(f"Recipe id: {recipe_id}")
    results_per_recipe = False
    for step_idx, step in enumerate(steps):
        result = re.search(pattern, step)
        if result:
            if not results_per_recipe:
                print("Results:")
                results_per_recipe = True

            print(f"Step {step_idx + 1}: {step}")

    if not results_per_recipe:
        print("No matching steps found")

    print("\n" + "-" * 40 + "\n")

Recipe id: 44123
No matching steps found

----------------------------------------

Recipe id: 67664
No matching steps found

----------------------------------------

Recipe id: 38798
No matching steps found

----------------------------------------

Recipe id: 35173
No matching steps found

----------------------------------------

Recipe id: 84797
No matching steps found

----------------------------------------

Recipe id: 44045
No matching steps found

----------------------------------------

Recipe id: 107229
No matching steps found

----------------------------------------

Recipe id: 95926
No matching steps found

----------------------------------------

Recipe id: 453467
No matching steps found

----------------------------------------

Recipe id: 306168
No matching steps found

----------------------------------------

Recipe id: 50662
No matching steps found

----------------------------------------

Recipe id: 118843
No matching steps found

------------------------------

In [84]:
pattern = r"^this[^A-Za-z0-9_]*\.{3}, ?but"

matches = recipes["description"].str.contains(pattern, na=False)

matched_recipes = recipes[matches.notna()]

print("Количество подходящих рецептов:", len(matched_recipes))
print("\nПримеры описаний:")
for i, row in matched_recipes.head(3).iterrows():
    print(row["description"])

Количество подходящих рецептов: 30000

Примеры описаний:
an original recipe created by chef scott meskan, george's at the cove. we enjoyed this when we visited this restaurant in la jolla, california. this recipe is requested so often, they have it printed and ready at the hostess stand. it's unbeatable at the restaurant, but i do a pretty good job at home, too, if i do say so myself!
my children and their friends ask for my homemade popsicles morning, noon and night. i never turn them down; who am i to tell them that they are good for them! for variety i substitute different flavours of frozen juice - grape, fruit punch, tropical etc.
these were so go, it surprised even me.


5\. В текстах шагов рецептов обыкновенные дроби имеют вид "a / b". Используя регулярные выражения, уберите в тексте шагов рецепта с id 72367 пробелы до и после символа дроби. Выведите на экран шаги этого рецепта после их изменения.

In [ ]:
pattern = '<step number=".*?" id="72367">(.*?)<\/step>'
step = re.findall(pattern, content, re.DOTALL)[0]

step = re.sub(r"(\d+)\s*/\s*(\d+)", r"\1/\2", step)

print(step)

### Сегментация текста

6\. Разбейте тексты шагов рецептов на слова при помощи пакета `nltk`. Посчитайте и выведите на экран кол-во уникальных слов среди всех рецептов. Словом называется любая последовательность алфавитных символов (для проверки можно воспользоваться `str.isalpha`). При подсчете количества уникальных слов не учитывайте регистр.

In [95]:
import nltk
from nltk.tokenize import word_tokenize

with open("data/steps_sample.xml", "r") as f:
    xml_string = f.read()

words = [word.lower() for word in word_tokenize(xml_string) if word.isalpha()]

unique_words = set(words)
num_unique_words = len(unique_words)

print(f"Всего слов: {len(words)}")
print(f"Уникальных слов: {num_unique_words}")

Всего слов: 3120421
Уникальных слов: 14929


7\. Разбейте описания рецептов из `recipes` на предложения при помощи пакета `nltk`. Найдите 5 самых длинных описаний (по количеству _предложений_) рецептов в датасете и выведите строки фрейма, соответствующие этим рецептами, в порядке убывания длины.

8\. Напишите функцию, которая для заданного предложения выводит информацию о частях речи слов, входящих в предложение, в следующем виде:
```
PRP   VBD   DT      NNS     CC   VBD      NNS        RB   
 I  omitted the raspberries and added strawberries instead
``` 
Для определения части речи слова можно воспользоваться `nltk.pos_tag`.

Проверьте работоспособность функции на названии рецепта с id 241106.

Обратите внимание, что часть речи должна находиться ровно посередине над соотвествующим словом, а между самими словами должен быть ровно один пробел.


In [102]:
import nltk

def pos_info(sentence):
    tagged_words = nltk.pos_tag(nltk.word_tokenize(sentence))
    for tag in tagged_words:
        print("{:<7}{}".format(tag[1], tag[0]), end=" ")

title = recipes.loc[recipes['id'] == 241106]['name'].values[0]
pos_info(title)

JJ     eggplant NNS    steaks IN     with NNS    chickpeas VBP    feta JJ     cheese CC     and JJ     black NNS    olives 